# Enrichment Analysis using Knetminer SPARQL with Jupyter

## Step 1: Import the libraries used in this script.

In [1]:
from enrichment_analysis_functions import *

import ipywidgets as widgets
from ipywidgets import interact, interact_manual

from IPython.display import HTML

In [3]:
# display full dataframe pandas
pd.set_option('display.max_rows', None)

## Step 2: Get the genes related to traits from the database

### Choose the Tax ID and get the list of related studies

Please note:
1. It take a couple of seconds to get the list of studies.
2. The only tax IDs that will generate a table of studies are:
    - 4565: Triticum aestivum (wheat)
    - 3702: Arabidopsis thaliana

In [6]:
taxID = ''
total_genes = 0
studyAcc = ''
choice = ''
#genes_list = []
dframe_GeneTrait = pd.DataFrame()
total_DEXgenes = set()

# create dataframe for Tax IDs and their names
dframe_taxID = df_taxID()

@interact_manual
def show_taxid(Species = dframe_taxID['Tax Names']):
    global taxID
    global total_genes
    global dframe_GeneTrait
    
    taxID = dframe_taxID[dframe_taxID['Tax Names'] == Species]['Tax IDs'].item()
    print("Tax ID is: " + taxID)
    
    total_genes = get_gene_count(taxID)
    
    # import csv for the tax ID
    dframe_GeneTrait = pd.read_csv (f'GeneTraitTable_{taxID}.csv',
                                usecols= ["Gene Accession", "Gene Name", "Trait Accession", "Trait Name",
                                          "Evidence", "Network URL"])
    
    dframe_GeneTrait = dframe_GeneTrait.drop_duplicates()
    
    
    print("\nDo you want to get the list of genes from a study or use your own list?")

    @interact_manual
    def show_study_list(Choice = ["Study", "List of Genes"]):
        global choice
        
        choice = Choice   
            
        if Choice == "Study":
            dframe_study_list = get_study_list(taxID)
            
            if dframe_study_list.shape[0] != 0:
                print("\nChoose from the list of studies related to the chosen Tax ID:")

                @interact_manual
                def get_study_list_for_triat(Study_Title = dframe_study_list['Study Title']):
                    global studyAcc
                    global total_DEXgenes
                    
                    studyAcc = dframe_study_list[dframe_study_list['Study Title'] == Study_Title]['Study Accession'].item()
                    print(" Study Accession is: " + studyAcc)
                    
                    total_DEXgenes = get_study_DEXgenes(studyAcc) # get unique set of genes

            else:
                print("No studies in the databse for the selected tax ID. Please provide your list of genes.")
            
            # get list of genes and print the final table
            
        else:
            print ("\nPlease paste the list of genes (separated by spaces).")
            @interact_manual
            def input_genes_list(genes = ''):
                #global genes_list
                global total_DEXgenes
                
                genes_list = genes.split()
                total_DEXgenes = set(genes_list) # get unique set of genes
                
                # get list of genes and print the final table
                
                print("\n" + str(len(total_DEXgenes)) + " genes provided:")
                for g in genes_list:
                    print(g)

interactive(children=(Dropdown(description='Species', options=('Triticum aestivum (wheat)', 'Arabidopsis thali…

In [7]:
print(taxID, total_genes, studyAcc, choice, len(total_DEXgenes))

4565 116503 E-MTAB-8520 Study 1717


### Import the CSV file containing genes and traits into a dataframe

## Step 3: Get the differentially expressed genes in a study

Create a function that will take dframe_GeneTrait and total_DEXgenes
Then:
print df_Ftest_Csorted
return dframe_GeneTrait_filtered, df_Ftest_Csorted

## Step 4: Use the list of genes from the study dataframe to extract their rows from the dframe_GeneTrait.

In [10]:
# Extract the rows containg the genes list from the first dataframe (dframe_GeneTrait)
dframe_GeneTrait_filtered = dframe_GeneTrait[dframe_GeneTrait['Gene Accession'].isin(total_DEXgenes)]

# Sort dframe_GeneTrait_filtered 
dframe_GeneTrait_filtered = dframe_GeneTrait_filtered.sort_values(['Trait Accession', 'Gene Name', 'Evidence'],
                                                                  ascending = [True, True, True])

# update the dataframe index
dframe_GeneTrait_filtered = dframe_GeneTrait_filtered.reset_index(drop=True)

#dframe_GeneTrait_filtered = dframe_GeneTrait_filtered.drop_duplicates()
#display (dframe_GeneTrait_filtered)


In [11]:
dframe_GeneTrait_filtered

Gene Accession           Gene Name        Trait Accession  \
0      TRAESCS5B02G335500                FAS1                0000061   
1      TRAESCS5A02G336500                FAS1                0000061   
2      TRAESCS5D02G341200                FAS1                0000061   
3      TRAESCS7A02G168100               HDG11                0000061   
4      TRAESCS7B02G073600                 PSP                0000061   
5      TRAESCS1D02G084400  TRAESCS1D02G084400                0000061   
6      TRAESCS2B02G122900               AGAL3                0000072   
7      TRAESCS2A02G334600                 AIH                0000072   
8      TRAESCS2B02G347800                 AIH                0000072   
9      TRAESCS2D02G328900                 AIH                0000072   
10     TRAESCS5D02G326200               APRR5                0000072   
11     TRAESCS3D02G260100               ARF14                0000072   
12     TRAESCS3D02G008500                 C50                0000072   
13     TRAESCS3D02G366600                 FD4                0000072   
14     TRAESCS5B02G058200                 H2B                0000072   
15     TRAESCS5A02G383800               HSFA2                0000072   
16     TRAESCS3D02G115400             HSP17.6                0000072   
17     TRAESCS7B02G347100             HSP17.6                0000072   
18     TRAESCS3A02G113100             HSP17.6                0000072   
19     TRAESCS3B02G130300             HSP17.6                0000072   
20     TRAESCS3B02G130900             HSP17.7                0000072   
21     TRAESCS3D02G114700             HSP17.7                0000072   
22     TRAESCS3B02G131100             HSP17.7                0000072   
23      TRAESCSU02G194600             HSP18.1                0000072   
24     TRAESCS6A02G316200             HSP23.6                0000072   
25      TRAESCSU02G116400             HSP70-9                0000072   
26     TRAESCS5B02G388900                LFG4                0000072   
27     TRAESCS3A02G251200               MYB26                0000072   
28     TRAESCS3A02G406000              NAC081                0000072   
29     TRAESCS5B02G380700               NET1D                0000072   
30     TRAESCS4B02G223000               NFYC1                0000072   
31     TRAESCS1D02G264500                  PI                0000072   
32     TRAESCS3A02G325500               PME57                0000072   
33     TRAESCS1A02G282900  TRAESCS1A02G282900                0000072   
34     TRAESCS1B02G390100  TRAESCS1B02G390100                0000072   
35     TRAESCS1B02G423500  TRAESCS1B02G423500                0000072   
36     TRAESCS1D02G084400  TRAESCS1D02G084400                0000072   
37     TRAESCS1D02G223200  TRAESCS1D02G223200                0000072   
38     TRAESCS1D02G403400  TRAESCS1D02G403400                0000072   
39     TRAESCS2B02G087400  TRAESCS2B02G087400                0000072   
40     TRAESCS2B02G360400  TRAESCS2B02G360400                0000072   
41     TRAESCS2D02G429500  TRAESCS2D02G429500                0000072   
42     TRAESCS3B02G019900  TRAESCS3B02G019900                0000072   
43     TRAESCS3B02G461900  TRAESCS3B02G461900                0000072   
44     TRAESCS4D02G035800  TRAESCS4D02G035800                0000072   
45     TRAESCS5A02G045300  TRAESCS5A02G045300                0000072   
46     TRAESCS5A02G446200  TRAESCS5A02G446200                0000072   
47     TRAESCS5B02G307600  TRAESCS5B02G307600                0000072   
48     TRAESCS5D02G055400  TRAESCS5D02G055400                0000072   
49     TRAESCS5D02G071500  TRAESCS5D02G071500                0000072   
50     TRAESCS6A02G041000  TRAESCS6A02G041000                0000072   
51     TRAESCS6A02G091400  TRAESCS6A02G091400                0000072   
52     TRAESCS6A02G259000  TRAESCS6A02G259000                0000072   
53     TRAESCS6B02G288000  TRAESCS6B02G288000                0000072   
54     TRAESCS6D02G221600  TRAESCS6D02G221600      

## Step 5: Enrichment Analysis using SciPy

In [12]:
# create dataframe to add the odd ratio and p-value
df_Ftest = pd.DataFrame (columns = ["Trait Accession", "Trait Name", "odds ratio", "exact p-value",
                                   "Total number of related genes in database",
                                    "Number of related genes in user/study list"])

# create list to add the Trait Accessions numbers
traits =  []

for x, row in dframe_GeneTrait_filtered.iterrows():
    trait_acc = row['Trait Accession']
    
    if trait_acc not in traits:
        
        traits.append(trait_acc)
        trait_name = row['Trait Name']
        
        # 1a. Get the complete set of genes linked to the trait in the gene list
        select_trait = dframe_GeneTrait_filtered.loc[dframe_GeneTrait_filtered['Trait Accession'] == trait_acc]
        
        # 1b. Get the distinct list of genes linked to the trait in the gene list
        trait_DEXgenes = set(select_trait['Gene Accession'].unique())
        
        
        # 2a. Get the complete set of genes linked to the trait in the database (dframe_GeneTrait)
        select_Totaltrait = dframe_GeneTrait.loc[dframe_GeneTrait['Trait Accession'] == trait_acc]
        
        # 2b. Get the distinct list of genes linked to the trait in dframe_GeneTrait
        total_TraitGenes = set(select_Totaltrait['Gene Accession'].unique())
        
        
        # 3. Calculate the odds ratio and p-value using scipy
        a= len(trait_DEXgenes)
        b= len(total_DEXgenes)-len(trait_DEXgenes)
        c= len(total_TraitGenes)-len(trait_DEXgenes)
        d= total_genes-a-b-c
        data = [[a, b], [c, d]]
        oddsratio, pvalue = stats.fisher_exact(data)
        
        # 4. Add the data to the table
        df = {'Trait Accession': trait_acc, 'Trait Name': trait_name, 'odds ratio': oddsratio, 'exact p-value': pvalue,
             'Total number of related genes in database': len(total_TraitGenes),
              'Number of related genes in user/study list': a}
        df_Ftest = df_Ftest.append(df, ignore_index = True)

In [13]:
df_Ftest

Trait Accession                                 Trait Name  \
0                  0000061                             Stem solidness   
1                  0000072                             Grain hardness   
2                  0000088                         Hessian fly damage   
3                  0000281                Common bunt spike incidence   
4               TO_0000004                  reversible male sterility   
5               TO_0000008                      potassium sensitivity   
6               TO_0000015                         oxygen sensitivity   
7               TO_0000019                            seedling height   
8               TO_0000027                                culm number   
9               TO_0000036                     hybrid incompatibility   
10              TO_0000040                             panicle length   
11              TO_0000043                      root morphology trait   
12              TO_0000050                    inflorescence branching   
13              TO_0000051                              stem strength   
14              TO_0000053                           pollen sterility   
15              TO_0000058                      herbicide sensitivity   
16              TO_0000069                            variegated leaf   
17              TO_0000071                        anthocyanin content   
18              TO_0000072                                 awn length   
19              TO_0000074                   blast disease resistance   
20              TO_0000075                          light sensitivity   
21              TO_0000078                            root dry weight   
22              TO_0000084                                root number   
23              TO_0000085                               leaf rolling   
24              TO_0000101                          broad-leaved weed   
25              TO_0000104                           floury endosperm   
26              TO_0000112                         disease resistance   
27              TO_0000115                          root mass density   
28              TO_0000124                            flag leaf angle   
29              TO_0000128                              harvest index   
30              TO_0000131                       leaf water potential   
31              TO_0000135                                leaf length   
32              TO_0000136                leaf relative water content   
33              TO_0000137                            days to heading   
34              TO_0000143                           relative biomass   
35              TO_0000146                                seed length   
36              TO_0000148                   viral disease resistance   
37              TO_0000149                                 seed width   
38              TO_0000152                             panicle number   
39              TO_0000158                      red light sensitivity   
40              TO_0000163                          auxin sensitivity   
41              TO_0000167                      cytokinin sensitivity   
42              TO_0000173                       ethylene sensitivity   
43              TO_0000180                         spikelet fertility   
44              TO_0000181                                seed weight   
45              TO_0000183                  other miscellaneous trait   
46              TO_0000187                               anther color   
47              TO_0000188                        drought sensitivity   
48              TO_0000190                            seed coat color   
49              TO_0000194                            globular embryo   
50              TO_0000196                            amylose content   
51              TO_0000199                       genic male sterility   
52              TO_0000200                               brittle culm   
53              TO_0000202                          germination ratio

### Calculate adjusted p-value

In [14]:
# Get the list of p-values from the dataframe
pvalues = df_Ftest['exact p-value'].tolist()
print(len(pvalues))

287


In [15]:
# get by_descend and adj_pvalues
by_descend, q = p_adjust_bh(pvalues)

# sort the table by the indecies (used in the formula)
df_Ftest_Csorted = df_Ftest.reindex(by_descend)

# add column to dataframe
df_Ftest_Csorted.insert(4, 'adj p-value', q)

# sort the dataframe according to adjusted p-value
df_Ftest_Csorted = df_Ftest_Csorted.sort_values(by=['adj p-value'])

# update the dataframe index
df_Ftest_Csorted = df_Ftest_Csorted.reset_index(drop=True)

df_Ftest_Csorted

Trait Accession                                 Trait Name  \
0               TO_0000430                           germination rate   
1               TO_0000190                            seed coat color   
2               TO_0000276                          drought tolerance   
3               TO_0006002                            proline content   
4               TO_0002661                            seed maturation   
5               TO_0000253                              seed dormancy   
6               TO_0000344                    days to flowering trait   
7               TO_0000112                         disease resistance   
8               TO_0006001                             salt tolerance   
9               TO_0006019                      floral organ identity   
10              TO_0006004                          raffinose content   
11              TO_0000319                            rubisco content   
12              TO_0006018                             organ identity   
13              TO_0006036                            stem elongation   
14              TO_0000043                      root morphology trait   
15              TO_0000495                        chlorophyll content   
16              TO_0000598                            protein content   
17              TO_0000259                             heat tolerance   
18              TO_0000290                          flavonoid content   
19              TO_0000397                                 grain size   
20              TO_0002657                           oxidative stress   
21              TO_0000128                              harvest index   
22              TO_0000734                               grain length   
23              TO_0000183                  other miscellaneous trait   
24              TO_0000707                             pericarp color   
25              TO_0000199                       genic male sterility   
26              TO_0000479                           acid sensitivity   
27              TO_0000486                                 seed color   
28              TO_0000615                  abscisic acid sensitivity   
29              TO_0000225                              stamen number   
30              TO_0020106               Indole-3-acetic acid content   
31                 0000281                Common bunt spike incidence   
32              TO_0006066                      leaf trichome density   
33              TO_0001015                        photosynthetic rate   
34              TO_0001017                       water use efficiency   
35              TO_0000004                  reversible male sterility   
36              TO_0000469                           days to maturity   
37              TO_0000207                               plant height   
38              TO_0006017                          meristem identity   
39              TO_0002703                 protist disease resistance   
40   TO_0000522;TO_0000523                        stomatal resistance   
41              TO_0000036                     hybrid incompatibility   
42              TO_0000163                          auxin sensitivity   
43              TO_0000366                   reproductive growth time   
44              TO_0000187                               anther color   
45              TO_0000437                             male sterility   
46              TO_0000519                              rooting depth   
47              TO_0000619                                   vivipary   
48              TO_0001013                        lateral root number   
49              TO_0001018                         transpiration rate   
50              TO_0000303                             cold tolerance   
51              TO_0000358                           female sterility   
52              TO_0000345                             seed viability   
53              TO_0000069                            variegated leaf

## Choose the trait to display related genes

In [19]:
@interact
def get_gene_list_for_triat(Trait_Name = sorted(df_Ftest_Csorted['Trait Name'].unique())):
    
    print(" Trait Accession is: " +
          str(df_Ftest_Csorted[df_Ftest_Csorted['Trait Name'] == Trait_Name]['Trait Accession'].item()))
    
    print(" Adjusted p-value is: " +
          str(df_Ftest_Csorted[df_Ftest_Csorted['Trait Name'] == Trait_Name]['adj p-value'].item()))
    
    df = dframe_GeneTrait_filtered.loc[dframe_GeneTrait_filtered['Trait Name'] == Trait_Name]
    df = df[["Gene Accession", "Gene Name", "Evidence", "Network URL"]]
    df = df.reset_index(drop=True)
    
    s = "View Network"
    df['Network URL'] = df['Network URL'].apply(lambda x: f'<a href="{x}">{s}</a>')
    
    print("\n Total number of related unique genes from \n user/study list of genes is: " +
          str(df_Ftest_Csorted[df_Ftest_Csorted['Trait Name'] == Trait_Name]['Number of related genes in user/study list'].item()))  

    return HTML(df.to_html(render_links=True, escape=False))

interactive(children=(Dropdown(description='Trait_Name', options=('1000-grain weight', 'Common bunt spike inci…

## Choose the gene to display related traits

In [20]:
@interact
def get_gene_list_for_triat(Gene_Name = sorted(dframe_GeneTrait_filtered['Gene Name'].unique())):
    
    df = dframe_GeneTrait_filtered.loc[dframe_GeneTrait_filtered['Gene Name'] == Gene_Name]
    df = df[["Gene Accession","Trait Accession", "Trait Name", "Evidence", "Network URL"]]
    #df = df.drop_duplicates()
    df = df.reset_index(drop=True)
    
    s = "View Network"
    df['Network URL'] = df['Network URL'].apply(lambda x: f'<a href="{x}">{s}</a>')
    
    print("\n Total number of related unique traits is: " + str(len(df['Trait Accession'].unique())))
    
    return HTML(df.to_html(render_links=True, escape=False))

interactive(children=(Dropdown(description='Gene_Name', options=('4CLL9', 'AAC1', 'AAE14', 'AAO1', 'AAP2', 'AB…

## The table below shows the meaning of the evidence codes
- A homologous gene (or homolog) is a gene inherited in two species by a common ancestor.
- Genetic interaction networks represent the functional interactions between pairs of genes.


In [6]:
df_evidence()

Evidence Code         Evidence Type  Homology  Interaction
0        TM_0-0      Text Mining (TM)         0            0
1        TM_0-1           Text Mining         0            1
2        TM_1-0           Text Mining         1            0
3        TM_1-1           Text Mining         1            1
4      GWAS_0-0  Genetic Study (GWAS)         0            0
5      GWAS_0-1         Genetic Study         0            1
6      GWAS_1-0         Genetic Study         1            0
7      GWAS_1-1         Genetic Study         1            1